## Preprocessando SINAN raw_data

### Dependências

In [56]:
import pandas as pd
import plotly.express as px
import numpy as np

### Carregando dados

In [57]:
SINAN_RAW_PATH = './../data/raw_data/2. SINAN (violencia sexual)/DadosViolSexualDomestica_2013-18_SINAN.csv'

In [58]:
%%time

# Apenas para testes (ler apenas as primeiras nrows linhas)
nrows = 100000

raw_dataframe = pd.read_csv(SINAN_RAW_PATH, nrows = nrows)

print('Número de colunas:', len(raw_dataframe.columns))
print('Número de linhas:', len(raw_dataframe))

Número de colunas: 158
Número de linhas: 100000
Wall time: 1.04 s


### Agrupamento de variáveis

#### Relação com agressor

In [59]:
def get_agressor_relationship(dataframe):

    '''
    Retorna uma lista das relações das vítimas com os agressores.

    Ex: ['Pai', 'Desconhecido', ..., 'N/A']
    '''

    relationship_dict = {
        'REL_PAI': 'Pai',
        'REL_MAE': 'Mãe',
        'REL_PAD': 'Padrasto',
        'REL_CONJ': 'Cônjugue',
        'REL_EXCON': 'Ex-cônjuge',
        'REL_NAMO': 'Namorado/a',
        'REL_EXNAM': 'Ex-namorado/a',
        'REL_FILHO': 'Filho/a',
        'REL_DESCO': 'Desconhecido',
        'REL_IRMAO': 'Irmão/ã',
        'REL_CONHEC': 'Amigo/a',
        'REL_CUIDA': 'Cuidador/a',
        'REL_PATRAO': 'Chefe',
        'REL_INST': 'Relação Institucional',
        'REL_POL': 'Policial/Agente da lei',
        'REL_PROPRI': 'Próprio/a',
        'REL_OUTROS': 'Outra pessoa',
        'REL_MAD': 'Madrasta'
    }

    agressor_relationship = []
    relationship_keys     = relationship_dict.keys()

    for index in dataframe.index:

        case = dataframe.loc[index]

        found_rel = False

        for key in relationship_keys:

            relantionship = relationship_dict[key]

            if case[key] == 1:

                agressor_relationship.append(relantionship)
                found_rel = True

                break

        if not found_rel:

            agressor_relationship.append('N/A')

    return agressor_relationship

def preprocess_relationship(value):
    
    if value == '*':
        return 0
    
    elif value == '':
        return 0

    else:
        
        try:
            return np.int8(value)
        
        except:
            
            try:
                return np.int8(float(value))
            
            except: # NaN variables
                return 0

In [60]:
%%time

# Corrigindo tipo das variáveis de relação

relationship_columns = ['REL_PAI','REL_MAE','REL_PAD','REL_CONJ','REL_EXCON',
                        'REL_NAMO','REL_EXNAM','REL_FILHO','REL_DESCO','REL_IRMAO',
                        'REL_CONHEC','REL_CUIDA','REL_PATRAO','REL_INST','REL_POL',
                        'REL_PROPRI','REL_OUTROS','REL_MAD']


for column in relationship_columns:

    # Convertendo valores para inteiros 
    raw_dataframe[column] = raw_dataframe[column].apply(preprocess_relationship)

Wall time: 1.46 s


In [61]:
%%time

raw_dataframe['AGRESSOR'] = get_agressor_relationship(raw_dataframe)

Wall time: 25.4 s


In [62]:
# Retirando dados omitidos
df  = raw_dataframe[raw_dataframe['AGRESSOR'] != 'N/A']

fig = px.histogram(df, x="AGRESSOR", title=f'Relação: Vítima x Agressor ({nrows} casos)')
fig.show()

### Tipo de violência

In [63]:
def get_violence(dataframe):

    '''
    Retorna uma lista do tipo de violência sofrida pela vítima.

    Ex: ['Pai', 'Desconhecido', ..., 'N/A']
    '''
    
    violence_dict = {
        'VIOL_FISIC': 'Física',
        'VIOL_PSICO': 'Psicológica',
        'VIOL_TORT': 'Tortura',
        'VIOL_SEXU': 'Sexual',
        'VIOL_TRAF': 'Tráfico humano',
        'VIOL_FINAN': 'Financeira/econômica',
        'VIOL_NEGLI': 'Negligência/abandono',
        'VIOL_INFAN': 'Trabalho infantil',
        'VIOL_LEGAL': 'Legal',
        'VIOL_OUTR': 'Outra',
    }

    type_violence  = []
    violence_keys  = violence_dict.keys()

    for index in dataframe.index:

        case = dataframe.loc[index]

        found_violence = False

        for key in violence_keys:

            violence = violence_dict[key]

            if case[key] == 1:

                type_violence.append(violence)
                found_violence = True

                break

        if not found_violence:

            type_violence.append('N/A')

    return type_violence

def preprocess_violence(value):
    
    if value == '*':
        return 0
    
    elif value == '':
        return 0

    else:
        
        try:
            return np.int8(value)
        
        except:
            
            try:
                return np.int8(float(value))
            
            except: # NaN variables
                return 0

In [64]:
%%time

# Corrigindo tipo das variáveis de violencia

violence_columns = ['VIOL_FISIC','VIOL_PSICO','VIOL_TORT','VIOL_SEXU',
                    'VIOL_TRAF','VIOL_FINAN','VIOL_NEGLI','VIOL_INFAN',
                    'VIOL_LEGAL','VIOL_OUTR']


for column in violence_columns:

    # Convertendo valores para inteiros 
    raw_dataframe[column] = raw_dataframe[column].apply(preprocess_violence)

Wall time: 832 ms


In [65]:
%%time

raw_dataframe['VIOLENCE'] = get_violence(raw_dataframe)

Wall time: 19.1 s


In [66]:
# Retirando dados omitidos
df  = raw_dataframe[raw_dataframe['VIOLENCE'] != 'N/A']

fig = px.histogram(df, x="VIOLENCE", title=f'Tipo de violência sofrida ({nrows} casos)')
fig.show()

### Raça do paciente

In [67]:
def preprocess_race(value):
    
    try:
        return np.int8(value)

    except:

        try:
            return np.int8(float(value))

        except: # NaN variables
            return 9

In [68]:
race_dict = {
    1: 'Branca',
    2: 'Preta',
    3: 'Amarela',
    4: 'Parda',
    5: 'Indígena',
    9: 'N/A'
}

raw_dataframe.CS_RACA = raw_dataframe.CS_RACA.apply(preprocess_race)
raw_dataframe.CS_RACA = raw_dataframe.CS_RACA.apply(lambda race_key: race_dict[race_key])

In [69]:
# Retirando dados omitidos
df  = raw_dataframe[raw_dataframe['CS_RACA'] != 'N/A']

fig = px.histogram(df, x="CS_RACA", title=f'Raças ({nrows} casos)')
fig.show()